# Quick start and SQL query example
This notebook shows how to use the pipeline and some example queries that can be made from the database. It has 3 sections:
1. Run the Pipeline and Populate the Database
2. Example SQL query
3. Visualize results

In [1]:
import sqlite3
import pandas as pd
import geopandas as gpd
import plotly.express as px
from carbon_stats import CarbonStats

# 1. Run the Pipeline and Populate the Database
Using the pipeline defined in carbon_stats.py, the following cell shows an example of running the pipeline.
This cell with takes 1 minute or more to run, mostly because the pipeline currently uses `raster_stats.zonal_stats`, which is simple to implement but slow with large rasters. If speed is important, I would look at using other approaches for calculating zonal stats such as `rioxarray`.

In [2]:
# Where the database file will be saved
db_file = "data/outputs/county_carbon.sqlite"

# Initialize the processor
cs = CarbonStats(
    raster_file="data/inputs/NLS_TotalEcosystemCarbon2020.tif",
    boundary_file="data/inputs/US_census_counties/cb_2024_us_county_500k.shp"
)

# Process the data
cs.read_raster()
cs.process_boundaries(['Michigan', 'Wisconsin', 'Minnesota'])
cs.calculate_stats()

# Export to database
cs.export_to_sqlite(db_file)

Successfully exported to data/outputs/county_carbon.sqlite


# 2. Example SQL query
Here's an example of reading from the database we just created.  Then, if we like, we can import it back to a GeoDataFrame.

In [3]:
#Connect to SQLite database file
conn = sqlite3.connect(db_file)

# Query all columns for Minnesota counties with more than 50 Tg CO2e
# Order from lowest to highest total_Tg_CO2e
query = """
SELECT *
FROM county_carbon
WHERE state_name = 'Minnesota'
  AND total_Tg_CO2e > 50
ORDER BY total_Tg_CO2e; 
"""

# Use pandas to execute query and load into DataFrame
df_from_sql = pd.read_sql_query(query, conn)

# Close the connection
conn.close()

# Transform df to a GeoDataFrame by recreating the geometry column
gdf_from_sql = gpd.GeoDataFrame(
    df_from_sql,
    geometry=gpd.GeoSeries.from_wkt(df_from_sql['geometry_wkt_EPSG_4326']),
    crs='EPSG:4326'
)
gdf_from_sql = gdf_from_sql.drop(columns='geometry_wkt_EPSG_4326')

# Output the GeoDataFrame to verify
gdf_from_sql.head()

geoid county_name state_name  total_Tg_CO2e  average_Mg_CO2e_per_acre  \
0  27135      Roseau  Minnesota      59.777109                 55.656440   
1  27097    Morrison  Minnesota      60.825771                 82.391388   
2  27111  Otter Tail  Minnesota      77.213624                 54.236593   
3  27017     Carlton  Minnesota      78.313274                139.839912   
4  27029  Clearwater  Minnesota      79.071139                119.910225   

   county_area_acres                                           geometry  
0       1.074038e+06  POLYGON ((-96.40541 48.99998, -96.20883 48.999...  
1       7.382540e+05  POLYGON ((-94.65346 46.34868, -94.65079 46.347...  
2       1.423644e+06  POLYGON ((-96.2812 46.63078, -96.24015 46.6308...  
3       5.600209e+05  POLYGON ((-93.0647 46.68009, -93.06457 46.6836...  
4       6.594195e+05  POLYGON ((-95.58289 48.02067, -95.22911 48.020...

# 3. Visualize results
Let's do an example of plotting and visualizing the results from the database. I'll run a different query that returns all counties, save it to a GeoDataFrame and then plot the results

## Build the dataframe for plotting from all available counties

In [4]:
#Connect to SQLite database file
conn = sqlite3.connect(db_file)

# Query all columns from county_carbon table
query = """
SELECT *
FROM county_carbon
"""

# Use pandas to execute query and load into DataFrame
df_from_sql = pd.read_sql_query(query, conn)

# Close the connection
conn.close()

# Transform df to a GeoDataFrame by recreating the geometry column
gdf = gpd.GeoDataFrame(
    df_from_sql,
    geometry=gpd.GeoSeries.from_wkt(df_from_sql['geometry_wkt_EPSG_4326']),
    crs='EPSG:4326'
)
gdf = gdf.drop(columns='geometry_wkt_EPSG_4326')
#Make a new column for county size in millions of acres
gdf["county_area_millions_acres"] = gdf["county_area_acres"] / 1000000

## Define a quick function for plotting

In [8]:
def make_carbon_map(gdf, carbon_statistic):  
    '''    Create a choropleth map of counties colored by the specified carbon statistic.'''
    labels = {
        "average_Mg_CO2e_per_acre": "Average CO2e Density (Mg/acre)",
        "total_Tg_CO2e": "Total CO2e (Tg)"
    }   
    title = f"Total Ecosystem Carbon by County: <br> {labels.get(carbon_statistic, carbon_statistic)}"
    
    fig = px.choropleth(
        gdf,
        geojson=gdf.geometry,
        locations=gdf.index,
        color=carbon_statistic,
        projection="mercator",
        color_continuous_scale="Viridis",
        custom_data=["county_name", "state_name", "total_Tg_CO2e", "county_area_millions_acres", "average_Mg_CO2e_per_acre"],
        labels=labels,
        width=600,
        # height=600,
        title=title,
    )

    fig.update_traces(
        hovertemplate=(
            "<b>%{customdata[0]}, %{customdata[1]}</b><br>" +
            "Total CO2e: %{customdata[2]:.1f} Tg<br>" +
            "County size: %{customdata[3]:.2f} million acres<br>" 
            "Average CO2e density: %{customdata[4]:.1f} Mg/acre<br>" +
            "<extra></extra>"
        )
    )
    fig.update_geos(fitbounds="locations", visible=False)
    fig.update_layout(margin=dict(l=0, r=0, t=10, b=0, pad=0),
                      title_y=0.95
                      )
    # fig.show()
    return fig

## Visualize 
This code creates an interactive plotly map where you can zoom in and out and hover over counties to see their data.  
  
**This plot may not be directly visible on GitHub.  If you wish to see the visualization, you have 3 options:**
1. **Download this Jupyter notebook** and view it on your own computer if you already have Jupyter Notebooks installed  
2. **Download the html file** for this chart and open it in your browser on your local computer. It is located in this repository at ['data/outputs/total_Tg_CO2e_carbon_map.html'](https://github.com/rumble-up/total-ecosystem-carbon/blob/main/data/outputs/total_Tg_CO2e_carbon_map.html) 
3. **Download and install the full repo** and then view this Jupyter notebook on your local computer.




In [9]:
fig = make_carbon_map(gdf, "total_Tg_CO2e")
fig.write_html("data/outputs/total_Tg_CO2e_carbon_map.html")
fig.show()

This coding challenge asked for the Total CO2e per county, but we can see in the chart above that larger counties typically have higher totals, just because they are larger.  In other words, they have more space for forests.  
In this case, St. Louis, Minnesota is highlighted in yellow has the highest total CO2e (580.3 Tg), but it's also the largest county (4.31 million acres).  
If we wanted to see which counties have the highest carbon density, we can plot the average MgCO2e per acre instead, as shown below.  
  
Now, one of the smallest counties, Menominee, Wisconsin has the highest carbon density and is highlighted in yellow with 250.4 Mg CO2e/acre. It consisently has a high carbon level throughout the county.  
The html for this figure can be downloaded from here and viewed in a browser on your local computer: ['data/outputs/average_Mg_CO2e_per_acre_carbon_map.html'](https://github.com/rumble-up/total-ecosystem-carbon/blob/main/data/outputs/average_Mg_CO2e_per_acre_carbon_map.html)

In [10]:
fig = make_carbon_map(gdf, "average_Mg_CO2e_per_acre")
fig.write_html("data/outputs/average_Mg_CO2e_per_acre_carbon_map.html")
fig.show()